# 1. Введение

In [8]:
# 1.1
# Пусть прибыль в вашей компании выражается следующей функцией, которая зависит от параметра  — количества производимых товаров:



# Найдите максимально возможную прибыль, которую вы можете получить, варьируя количество произведённых товаров.

import sympy
from sympy import solveset, Eq, Symbol
x = sympy.Symbol("x")
f = -x**4+6*x**3-4*x**2+80
d = f.diff()
print(solveset(Eq(d, 0), x))
f.subs(x,4)

{0, 1/2, 4}


144

In [9]:
# 1.4
13**2+2*7**2

267

# 2. Градиентный спуск: применение и модификации

In [4]:
# 2.7

# Загрузите стандартный датасет об алмазах из библиотеки Seaborn:
import seaborn as sns
import pandas as pd
df = sns.load_dataset('diamonds')

#Удалите часть признаков:

df.drop(['depth', 'table', 'x', 'y', 'z'], axis=1, inplace=True)

In [6]:
# Закодируйте категориальные признаки:

df = pd.get_dummies(df, drop_first=True)
df

carat  price  cut_Premium  cut_Very Good  cut_Good  cut_Fair  color_E  \
0       0.23    326            0              0         0         0        1   
1       0.21    326            1              0         0         0        1   
2       0.23    327            0              0         1         0        1   
3       0.29    334            1              0         0         0        0   
4       0.31    335            0              0         1         0        0   
...      ...    ...          ...            ...       ...       ...      ...   
53935   0.72   2757            0              0         0         0        0   
53936   0.72   2757            0              0         1         0        0   
53937   0.70   2757            0              1         0         0        0   
53938   0.86   2757            1              0         0         0        0   
53939   0.75   2757            0              0         0         0        0   

       color_F  color_G  color_H  color_I  color_J  clarity_VVS1  \
0            0        0        0        0        0             0   
1            0        0        0        0        0             0   
2            0        0        0        0        0             0   
3            0        0        0        1        0             0   
4            0        0        0        0        1             0   
...        ...      ...      ...      ...      ...           ...   
53935        0        0        0        0        0             0   
53936        0        0        0        0        0             0   
53937        0        0        0        0        0             0   
53938        0        0        1        0        0             0   
53939        0        0        0        0        0             0   

       clarity_VVS2  clarity_VS1  clarity_VS2  clarity_SI1  clarity_SI2  \
0                 0            0            0            0            1   
1                 0            0            0            1            0   
2                 0            1            0            0            0   
3                 0            0            1            0            0   
4                 0            0            0            0            1   
...             ...          ...          ...          ...          ...   
53935             0            0            0            1            0   
53936             0            0            0            1            0   
53937             0            0            0            1            0   
53938             0            0            0            0            1   
53939             0            0            0            0            1   

       clarity_I1  
0               0  
1               0  
2               0  
3               0  
4               0  
...           ...  
53935           0  
53936           0  
53937           0  
53938           0  
53939           0  

[53940 rows x 19 columns]

In [8]:
# Логарифмируйте признаки:
import numpy as np
df['carat'] = np.log(1+df['carat'])
df['price'] = np.log(1+df['price'])

In [9]:
# Определите целевую переменную и предикторы:

X_cols = [col for col in df.columns if col!='price'] 
X = df[X_cols]
y = df['price']

In [20]:
# Разделите выборку на обучающую и тестовую (объём тестовой возьмите равным 0.33), 
# значение random_state должно быть равно 42.
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42)

In [21]:
# Теперь реализуйте алгоритм линейной регрессии со стохастическим градиентным спуском (класс SGDRegressor). 
# Отберите с помощью GridSearchCV оптимальные параметры по следующей сетке:

# "loss": ["squared_error", "epsilon_insensitive"],
# "penalty": ["elasticnet"],
# "alpha": np.logspace(-3, 3, 15),
# "l1_ratio": np.linspace(0, 1, 11),
# "max_iter": np.logspace(0, 3, 10).astype(int),
# "random_state": [42],
# "learning_rate": ["constant"],
# "eta0": np.logspace(-4, -1, 4)

from sklearn.linear_model import SGDRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error


parameters = {
    "loss": ["squared_error", "epsilon_insensitive"],
    "penalty": ["elasticnet"],
    "alpha": np.logspace(-3, 3, 15),
    "l1_ratio": np.linspace(0, 1, 11),
    "max_iter": np.logspace(0, 3, 10).astype(int),
    "learning_rate": ["constant"],
    "eta0": np.logspace(-4, -1, 4)
}

sgd = SGDRegressor(random_state=42)
sgd_cv = GridSearchCV(estimator=sgd, param_grid=parameters, n_jobs=-1)
sgd_cv.fit(X_train, y_train)

print(sgd_cv.best_params_)

sgd = SGDRegressor(**sgd_cv.best_params_, random_state = 42)

sgd.fit(X_train, y_train)
sgd.score(X_train, y_train) # r2
ls = sgd.predict(X_test)

round(mean_squared_error(y_test, ls), 3)

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:1527: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:1527: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:1527: ConvergenceWarning: Maximum number of iteration reached before convergence. Consider increasing max_iter to improve the fit.
  warnings.warn(
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/linear_model/_stochastic_gradient.py:1527: ConvergenceWarning: Maximum number of iteration re

{'alpha': 0.0026826957952797246, 'eta0': 0.001, 'l1_ratio': 0.0, 'learning_rate': 'constant', 'loss': 'epsilon_insensitive', 'max_iter': 21, 'penalty': 'elasticnet'}


0.043

In [25]:
# 3.1
# Найдите третий корень полинома , взяв за точку старта 0.7. 
# Введите получившееся значение с точностью до трёх знаков после точки-разделителя.

# Попробуйте реализовать алгоритм с использованием Python на основе алгоритма градиентного спуска, изученного в предыдущем модуле.

def f(x):
    return 6*x**5-5*x**4-4*x**3+3*x**2
def dif(x):
    return 30*x**4-20*x**3-12*x**2+6*x

x0 = (0.7)
gamma = 0.01
x_cur = x0

vals = []
coords = []
i = 0
while True:
    x_new = x_cur - f(x_cur)/dif(x_cur)
    if x_new==x_cur:
        break
    x_cur = x_new
    vals.append(f(x_cur))
    coords.append(x_cur)
    i += 1
    print(f"iter={i}; x=({x_cur:.4f});"
          f" f(x)={f(x_cur):.4f}")

iter=1; x=(0.6296); f(x)=-0.0012
iter=2; x=(0.6287); f(x)=-0.0000
iter=3; x=(0.6287); f(x)=-0.0000
iter=4; x=(0.6287); f(x)=0.0000


In [27]:
def func1(x):
    return 3*x**2 - 6*x -45
def func2(x):
    return 6*x - 6


initial_value = 42
iter_count = 0
x_curr = initial_value
epsilon = 0.0001
f = func1(x_curr)

while (abs(f) > epsilon):
    f = func1(x_curr)
    f_prime = func2(x_curr)
    x_curr = x_curr - (f)/(f_prime)
    iter_count += 1
    print(x_curr)

#21.695121951219512
#11.734125501243229
#7.1123493600499685
#5.365000391507974
#5.015260627016227
#5.000029000201801
#5.000000000105126
#5.0

21.695121951219512
11.734125501243229
7.1123493600499685
5.365000391507974
5.015260627016227
5.000029000201801
5.000000000105126
5.0


In [28]:
def newtons_method(f, der, eps, init):
    iter_count = 0
    x_curr = init
    f = f(x_curr)
    while (abs(f) > eps):
        f = f(x_curr)
        f_der = der(x_curr)
        x_curr = x_curr - (f)/(f_prime)
        iter_count += 1
    return x_curr
 
from scipy.optimize import newton
newton(func=func1,x0=50,fprime=func2, tol=0.0001)

5.0

In [29]:
# 3.6
# Дана функция . Найдите решение уравнения  для поиска корня в окрестностях точки . 
# Ответ округлите до трёх знаков после точки-разделителя.
# f = x**3-72*x-220

def func(x):
    return x**3-72*x-220
def func1(x):
    return 3*x**2 - 72


initial_value = 12
iter_count = 0
x_curr = initial_value
epsilon = 0.0001
f = func(x_curr)

while (abs(f) > epsilon):
    f = func(x_curr)
    f_prime = func1(x_curr)
    x_curr = x_curr - (f)/(f_prime)
    iter_count += 1
    print(x_curr)

10.21111111111111
9.756461564762278
9.727252176332618
9.72713442131889
9.727134419408875


In [31]:
# 3.7
# Найдите положительный корень для уравнения f = x**2+9*x-5.

# В качестве стартовой точки возьмите 2.2.

# Расчёт произведите поэтапно или с помощью Python.

# Ответ округлите до двух знаков после точки-разделителя

def func(x):
    return x**2+9*x-5
def func1(x):
    return 2*x+9


initial_value = 2.2
iter_count = 0
x_curr = initial_value
epsilon = 0.01
f = func(x_curr)

while (abs(f) > epsilon):
    f = func(x_curr)
    f_prime = func1(x_curr)
    x_curr = x_curr - (f)/(f_prime)
    iter_count += 1
    print(x_curr)

0.7343283582089555
0.5291259698087832
0.5249395544696249
0.5249378105607477


In [32]:
# 3.9
# С помощью метода Ньютона найдите точку минимума для функции 8*x**3-2*x**2-450.

# Для расчётов используйте Python.

# В качестве стартовой точки возьмите , точность примите за .

# Ответ округлите до трёх знаков после точки-разделителя.

def func1(x):
    return 24*x**2-4*x
def func2(x):
    return 48*x-4


initial_value = 42
iter_count = 0
x_curr = initial_value
epsilon = 0.0001
f = func1(x_curr)

while (abs(f) > epsilon):
    f = func1(x_curr)
    f_prime = func2(x_curr)
    x_curr = x_curr - (f)/(f_prime)
    iter_count += 1
    print(x_curr)

21.041749502982107
10.562707090133793
5.323351550447383
2.7040050774153417
1.3949941413301903
0.7418109325525483
0.41784523900811205
0.26096925221473555
0.19169814030401197
0.16955770984744145
0.1667151339969682
0.1666666807529666
0.16666666666666785


# 4. Квазиньютоновские методы

### схема Бройдена — Флетчера — Гольдфарба — Шанно (BFGS).

In [33]:
import numpy as np
from scipy.optimize import minimize

In [34]:
# Определим функцию, которую будем оптимизировать. Вместо отдельных x и y можно взять координаты единого вектора:

def func(x):
    return x[0]**2.0 + x[1]**2.0

In [35]:
# Теперь определим градиент для функции:

def grad_func(x):
    return np.array([x[0] * 2, x[1] * 2])

In [36]:
# Зададим начальную точку:

x_0 = [1.0, 1.0]

In [37]:
# Определим алгоритм:

result = minimize(func, x_0, method='BFGS', jac=grad_func)

In [38]:
# Выведем результаты:

print('Статус оптимизации %s' % result['message'])
print('Количество оценок: %d' % result['nfev'])
solution = result['x']
evaluation = func(solution)
print('Решение: f(%s) = %.5f' % (solution, evaluation))
 
#Статус оптимизации Optimization terminated successfully.
#Количество оценок: 3
#Решение: f([0. 0.]) = 0.00000

Статус оптимизации Optimization terminated successfully.
Количество оценок: 3
Решение: f([0. 0.]) = 0.00000


In [39]:
# Можно повторить то же самое с вариацией  L-BFGS-B:

# определяем нашу функцию
def func(x):
    return x[0]**2.0 + x[1]**2.0
 
#  определяем градиент функции
def grad_func(x):
    return np.array([x[0] * 2, x[1] * 2])
 
# определяем начальную точку
x_0 = [1, 1]
# реализуем алгоритм L-BFGS-B
result = minimize(func, x_0, method='L-BFGS-B', jac=grad_func)
# получаем результат
print('Статус оптимизации %s' % result['message'])
print('Количество оценок: %d' % result['nfev'])
solution = result['x']
evaluation = func(solution)
print('Решение: f(%s) = %.5f' % (solution, evaluation))

Статус оптимизации CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL
Количество оценок: 3
Решение: f([0. 0.]) = 0.00000


In [42]:
# 4.1
# Найдите точку минимума для функции .

# В качестве стартовой возьмите точку (-400,-400).

# Значения координат округлите до целого числа

# определяем нашу функцию
def func(x):
    return x[0]**2-x[0]*x[1]+x[1]**2+9*x[0]-6*x[1]+20
 
#  определяем градиент функции
def grad_func(x):
    return np.array([x[0]*2-x[1]+9, x[1] * 2-x[0]-6])
 
# определяем начальную точку
x_0 = [-400, -400]
# реализуем алгоритм BFGS
result = minimize(func, x_0, method='BFGS', jac=grad_func)
# получаем результат
print('Статус оптимизации %s' % result['message'])
print('Количество оценок: %d' % result['nfev'])
solution = result['x']
evaluation = func(solution)
print('Решение: f(%s) = %.5f' % (solution, evaluation))

Статус оптимизации Optimization terminated successfully.
Количество оценок: 11
Решение: f([-4.  1.]) = -1.00000


In [44]:
# 4.4
# Найдите минимум функции  с помощью квазиньютоновского метода BFGS.

# В качестве стартовой точки возьмите .

# В качестве ответа введите минимальное значение функции в достигнутой точке.

# определяем нашу функцию
def func(x):
    return x**2-3*x+45
 
#  определяем градиент функции
def grad_func(x):
    return 2*x-3
 
# определяем начальную точку
x_0 = 10
# реализуем алгоритм BFGS
result = minimize(func, x_0, method='L-BFGS-B', jac=grad_func)
# получаем результат
print('Статус оптимизации %s' % result['message'])
print('Количество оценок: %d' % result['nfev'])
solution = result['x']
evaluation = func(solution)
print('Решение: f(%s) = %.5f' % (solution, evaluation))

Статус оптимизации CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL
Количество оценок: 3
Решение: f([1.5]) = 42.75000


In [47]:
# 4.7
# Найдите минимум функции , взяв за стартовую точку .

# Какой алгоритм сошелся быстрее?

# определяем нашу функцию
def func(x):
    return x[0]**4+6*x[1]**2+10
 
#  определяем градиент функции
def grad_func(x):
    return np.array([4*x[0]**3, 12*x[1]])
 
# определяем начальную точку
x_0 = [100, 100]
# реализуем алгоритм BFGS
result = minimize(func, x_0, method='BFGS', jac=grad_func)
# получаем результат
print('Статус оптимизации %s' % result['message'])
print('Количество оценок: %d' % result['nfev'])
solution = result['x']
evaluation = func(solution)
print('Решение: f(%s) = %.5f' % (solution, evaluation))

Статус оптимизации Optimization terminated successfully.
Количество оценок: 37
Решение: f([1.31617159e-02 6.65344582e-14]) = 10.00000


# 6. Практика: линейное программирование

### Пример № 1. SciPy (scipy.optimize.linprog)

У нас есть 6 товаров с заданными ценами на них и заданной массой.  
  
Вместимость сумки, в которую мы можем положить товары, заранее известна и равна 15 кг.  
  
Какой товар и в каком объёме необходимо взять, чтобы сумма всех цен товаров была максимальной?  

In [50]:
# Создадим переменные на основе предложенных данных:

values = [4, 2, 1, 7, 3, 6] #стоимости товаров
weights = [5, 9, 8, 2, 6, 5] #вес товаров
C = 15 #вместимость сумки
n = 6 #количество товаров

In [52]:
# Здесь нам необходимо вспомнить линейную алгебру, так как очень важно, 
# чтобы векторы были в нужных нам размерностях, иначе мы не сможем использовать матричное умножение. 
# Вектор  размера  мы превращаем в матрицу размера (1,6) с помощью функции expand_dims(). Создаём все необходимые переменные:

c = - np.array(values) #изменяем знак, чтобы перейти от задачи максимизации к задаче минимизации
A = np.array(weights)  #конвертируем список с весами в массив
A = np.expand_dims(A, 0) #преобразуем размерность массива
b = np.array([C]) #конвертируем вместимость в массив

In [53]:
# Передаём подготовленные переменные в оптимизатор SciPy:

from scipy.optimize import linprog
linprog(c=c, A_ub=A, b_ub=b)

     con: array([], dtype=float64)
     fun: -52.50000000003076
 message: 'Optimization terminated successfully.'
     nit: 5
   slack: array([-2.24922303e-11])
  status: 0
 success: True
       x: array([6.18738515e-14, 1.05853303e-12, 1.21475940e-13, 7.50000000e+00,
       4.00246681e-13, 4.71394149e-13])

### Пример № 2. CVXPY



Снова решим задачу из примера № 1, но уже предположим, что товары нельзя дробить, и будем решать задачу целочисленного линейного программирования.  
  
SciPy не умеет решать такие задачи, поэтому будем использовать новую библиотеку CVXPY.  

In [56]:
import cvxpy

ModuleNotFoundError: No module named 'cvxpy'

In [54]:
x = cvxpy.Variable(shape=n, integer = True)

NameError: name 'cvxpy' is not defined

In [ ]:
# Далее зададим ограничения, используя матричное умножение:

constraint = (A @ x <= b)
total_value = c * x

In [ ]:
# Переходим непосредственно к решению задачи:

problem = cvxpy.Problem(cvxpy.Minimize(total_value), constraints=[constraint])

In [ ]:
# Вызываем получившееся решение:

problem.solve()

In [ ]:
# В результате получаем бесконечность. Это совершенно нереалистично.

# В таком случае будем рассматривать только положительные значения :



# В переформулированном виде задача будет решаться следующим образом:

x = cvxpy.Variable(shape=n, integer=True)
constraint = (A @ x <= b)
x_positive = (x >= 0)
total_value = c * x
problem = cvxpy.Problem(cvxpy.Minimize(total_value), constraints=[constraint, x_positive])
problem.solve()
x.value
 
#array([0., 0., 0., 7., 0., 0.])

In [ ]:
# А что если мы можем брать не любое количество товаров, а только один или не брать их вовсе? Задаём  типа boolean.


# и
# л
# и

# Программное решение такой задачи имеет следующий вид:

x = cvxpy.Variable(shape=n, boolean=True)
constraint = A @ x <= b
x_positive = x >= 0
total_value = c * x
problem = cvxpy.Problem(cvxpy.Minimize(total_value), constraints=[constraint, x_positive])
problem.solve()
#-17.0
x.value
#array([1., 0., 0., 1., 0., 1.])

### Пример № 3. PuLP

В нашей каршеринговой компании две модели автомобилей: модель A и модель B. Автомобиль A даёт прибыль в размере 20 тысяч в месяц, а автомобиль B — 45 тысяч в месяц. Мы хотим заказать на заводе новые автомобили и максимизировать прибыль. Однако на производство и ввод в эксплуатацию автомобилей понадобится время:  

* Проектировщику требуется 4 дня, чтобы подготовить документы для производства каждого автомобиля типа A, и 5 дней — для каждого автомобиля типа B.  
* Заводу требуется 3 дня, чтобы изготовить модель A, и 6 дней, чтобы изготовить модель B.  
* Менеджеру требуется 2 дня, чтобы ввести в эксплуатацию в компании автомобиль A, и 7 дней —  автомобиль B.  
* Каждый специалист может работать суммарно 30 дней.  

In [59]:
from pulp import *

In [67]:
problem = LpProblem('Производство машин', LpMaximize)
A = LpVariable('Автомобиль A', lowBound=0 , cat=LpInteger)
B = LpVariable('Автомобиль B', lowBound=0 , cat=LpInteger)
#Целевая функция
problem += 20000*A + 45000*B 
#Ограничения
problem += 4*A + 5*B <= 30 
problem += 3*A + 6*B <=30
problem += 2*A + 7*B <=30
problem.solve()
print("Количество автомобилей модели А: ", A.varValue)
print("Количество автомобилей модели В: ", B.varValue)
print("Суммарный доход: ", value(problem.objective))
#Количество автомобилей модели А:  1.0
#Количество автомобилей модели В:  4.0
#Суммарный доход:  200000.0


Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/tp/mcxy8wd524b65_m2_4n493dh0000gn/T/512e44a1cadb4fc5a2e876ee53240424-pulp.mps max timeMode elapsed branch printingOptions all solution /var/folders/tp/mcxy8wd524b65_m2_4n493dh0000gn/T/512e44a1cadb4fc5a2e876ee53240424-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 8 COLUMNS
At line 21 RHS
At line 25 BOUNDS
At line 28 ENDATA
Problem MODEL has 3 rows, 2 columns and 6 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 216667 - 0.00 seconds
Cgl0004I processed model has 3 rows, 2 columns (2 integer (0 of which binary)) and 6 elements
Cutoff increment increased from 1e-05 to 5000
Cbc0012I Integer solution of -195000 found by DiveCoefficient after 0 iterations and 0 nodes (0.01 s

In [68]:
# 6.1
# Составьте оптимальный план перевозок со склада № 1 и склада № 2 в три торговых центра с учётом тарифов, 
# запасов на складах и потребностей торговых центров, которые указаны в таблице:

# Сформулируйте предложенную задачу как задачу линейного программирования и решите её любым способом (желательно программным).

# В качестве ответа введите минимальную суммарную стоимость поставки. Ответ округлите до целого числа.

problem = LpProblem('Перевозки со складов', LpMinimize)
a1 = LpVariable('Склад A - ТЦ 1', lowBound=0 , cat=LpInteger)
a2 = LpVariable('Склад A - ТЦ 2', lowBound=0 , cat=LpInteger)
a3 = LpVariable('Склад A - ТЦ 3', lowBound=0 , cat=LpInteger)
b1 = LpVariable('Склад B - ТЦ 1', lowBound=0 , cat=LpInteger)
b2 = LpVariable('Склад B - ТЦ 2', lowBound=0 , cat=LpInteger)
b3 = LpVariable('Склад B - ТЦ 3', lowBound=0 , cat=LpInteger)
#Целевая функция
problem += 2*a1+5*a2+3*a3+7*b1+7*b2+6*b3
#Ограничения
problem += a1+b1 ==110
problem += a2+b2 ==150
problem += a3+b3 ==140
problem += a1+a2+a3 <=180
problem += b1+b2+b3 <=220
problem.solve()
print("a1: ",a1.varValue)
print("a2: ",a2.varValue)
print("a3: ",a3.varValue)
print("b1: ",b1.varValue)
print("b2: ",b2.varValue)
print("b3: ",b3.varValue)
print("Суммарный доход: ", value(problem.objective))

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/pulp/solverdir/cbc/osx/64/cbc /var/folders/tp/mcxy8wd524b65_m2_4n493dh0000gn/T/6134e54518764dca9fff33c5c364306a-pulp.mps timeMode elapsed branch printingOptions all solution /var/folders/tp/mcxy8wd524b65_m2_4n493dh0000gn/T/6134e54518764dca9fff33c5c364306a-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 10 COLUMNS
At line 41 RHS
At line 47 BOUNDS
At line 54 ENDATA
Problem MODEL has 5 rows, 6 columns and 12 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 1900 - 0.00 seconds
Cgl0004I processed model has 3 rows, 4 columns (4 integer (0 of which binary)) and 8 elements
Cutoff increment increased from 1e-05 to 0.9999
Cbc0012I Integer solution of 1900 found by DiveCoefficient after 0 iterations and 0 nodes (0.00 second

# 7. Дополнительные методы оптимизации. Практика

### МЕТОД ИМИТАЦИИ ОТЖИГА